# Pipeline d'entraînement des modèles NER avec spaCy (Google colab)

Auteur : Lucas Terriel

Date : 27/10/2021

Exécuter ce notebook dans une environnement GPU `Exécution > Modifier le type d'éxecution > accélérateur matériel : GPU`


### 1. Commencer par monter votre espace *drive* / dossier pour placer vos données (persistence)

L'organisation dans le *drive* ou le dossier peut suivre la structure suivante : 

```
drive/MyDrive
  |
  |- spaCy/
  |   |- data/ (contient les exemples ici train.spacy et le test.spacy et eval.spacy (opt.))
  |   |- le fichier base_config_nom.cfg selon l'architecture modèle utilisée 
  |   |- output_models/ : un dossier d'acceuil pour les modèles
  |           |- version_projet
  |           |       |- evaluations/ (metrics/ et visualisations/) 
  |           |- model1, model2 ...
  |   |- raw_texts_tests/ : un ou deux fichiers texte brutes pour tester le modèle "à la volée"
  |   |- vectors/ : fr_wiki fasttext embeddings (optionnel)
  |
```

In [ ]:
#from google.colab import drive
#drive.mount("/drive")

Mounted at /drive


### 2. Installer les dépendances Python

In [ ]:
# Use this if use GPU :
#!pip install -U pip setuptools wheel
#!pip install -U spacy[cuda111,transformers]
#!pip install torch
#!python -m spacy download fr_dep_news_trf
#!python -m spacy download fr_core_news_lg

# Use this if use CPU :
!pip install -U pip setuptools wheel
!pip install -U spacy
!python -m spacy download fr_core_news_lg

     |████████████████████████████████| 1.7 MB 12.9 MB/s 
     |████████████████████████████████| 946 kB 53.4 MB/s 
  Attempting uninstall: setuptools
    Found existing installation: setuptools 57.4.0
    Uninstalling setuptools-57.4.0:
      Successfully uninstalled setuptools-57.4.0
  Attempting uninstall: pip
    Found existing installation: pip 21.1.3
    Uninstalling pip-21.1.3:
      Successfully uninstalled pip-21.1.3
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
datascience 0.10.6 requires folium==0.2.1, but you have folium 0.8.3 which is incompatible.


     |████████████████████████████████| 5.9 MB 13.3 MB/s            
     |████████████████████████████████| 627 kB 40.6 MB/s            
     |████████████████████████████████| 42 kB 1.4 MB/s             
     |████████████████████████████████| 10.1 MB 26.6 MB/s            
     |████████████████████████████████| 451 kB 50.0 MB/s            
     |████████████████████████████████| 42 kB 1.2 MB/s             
     |████████████████████████████████| 2.6 MB 17.4 MB/s            
     |████████████████████████████████| 998 kB 41.0 MB/s            
     |████████████████████████████████| 3.3 MB 38.2 MB/s            
     |████████████████████████████████| 596 kB 46.9 MB/s            
     |████████████████████████████████| 895 kB 45.8 MB/s            
  Attempting uninstall: catalogue
    Found existing installation: catalogue 1.0.0
    Uninstalling catalogue-1.0.0:
      Successfully uninstalled catalogue-1.0.0
  Attempting uninstall: srsly
    Found existing installation: srsly 1.0.5
   

### 3. Vérifier Spacy en version 3.x et l'utilisation du GPU

In [ ]:
#import spacy 
#import torch
#torch.cuda.empty_cache()

#print('GPU State : ', spacy.prefer_gpu())
#print('GPU required : ', spacy.require_gpu(0))
#print('Cuda available : ', torch.cuda.is_available())
print('SPACY VERSION : ', spacy.__version__)

GPU State :  True
GPU required :  True
Cuda available :  True
SPACY VERSION :  3.1.3


### 4. Renseigner les paramètres d'accès à vos données

In [ ]:
# a modifier selon où se trouve les données

CONFIG_BASE="/drive/MyDrive/spaCy/base_config_cnn.cfg"
CONFIG_BASE_FILLED="/drive/MyDrive/spaCy/config_spacy_cnn.cfg"

OUTPUT_MODEL="/drive/MyDrive/spaCy/output_models/v1_n4a/n4a_v1_lg_cnn_fr"

### ➹ 5a. créer les vecteurs de mots (*embeddings*) [Optionnel si déjà réalisé]

In [ ]:
# !python -m spacy init vectors fr /drive/MyDrive/spaCy/vectors/wiki.fr.vec.txt.zip /drive/MyDrive/spaCy/vectors/vec_wikifr --name with_frwiki_vec --verbose

ℹ Creating blank nlp object for language 'fr'
[2021-10-26 09:16:08,274] [INFO] Reading vectors from /drive/MyDrive/spaCy/vectors/wiki.fr.vec.txt.zip
tcmalloc: large alloc 1382940672 bytes == 0x55e90da40000 @  0x7f3e972e1001 0x7f3e94ddf54f 0x7f3e94e2fb58 0x7f3e94e33b17 0x7f3e94ed2203 0x55e90386a544 0x55e90386a240 0x55e9038de627 0x55e90386bafa 0x55e9038d9915 0x55e9038d8ced 0x55e90386bbda 0x55e9038da737 0x55e9038d89ee 0x55e9037aae2b 0x55e9038dafe4 0x55e9038d8ced 0x55e9037aae2b 0x55e9038dafe4 0x55e9038d89ee 0x55e90386c48c 0x55e90386c698 0x55e9038dafe4 0x55e90386bafa 0x55e9038d9c0d 0x55e9038d8ced 0x55e90386bbda 0x55e9038d9c0d 0x55e9038d8ced 0x55e90386bbda 0x55e9038d9c0d
1152449it [02:27, 7802.89it/s]
[2021-10-26 09:18:37,336] [INFO] Loaded vectors from /drive/MyDrive/spaCy/vectors/wiki.fr.vec.txt.zip
✔ Successfully converted 1152449 vectors
✔ Saved nlp object with vectors to output directory. You can now use
the path to it in your config as the 'vectors' setting in [initialize].
/drive/MyDr

### ⚙️ 5b. Préparer le fichier de configuration [Optionnel si déjà réalisé]

Dans le fichier de config renseigner les variables `train` et `dev` (`vectors.path` optionnel) pour indiquer le chemin vers vos données d'entraînement puis lacer la cellule ci-dessous.

In [ ]:
# if use transformer with embeddings
#import os
#os.environ["TOKENIZERS_PARALLELISM"] = "false"

In [ ]:
!python -m spacy init fill-config $CONFIG_BASE $CONFIG_BASE_FILLED

✔ Auto-filled config with all values
✔ Saved config
/drive/MyDrive/spaCy/config_spacy_cnn.cfg
You can now add your data and train your pipeline:
python -m spacy train config_spacy_cnn.cfg --paths.train ./train.spacy --paths.dev ./dev.spacy


### 6. ✅ Contrôle des données d'entraînement

In [ ]:
!python -m spacy debug data $CONFIG_BASE_FILLED


============================ Data file validation ============================
✔ Pipeline can be initialized with data
✔ Corpus is loadable

=============================== Training stats ===============================
Language: fr
Training pipeline: tok2vec, ner
1205 training docs
266 evaluation docs
⚠ 51 training examples also in evaluation data
⚠ Low number of examples to train a new pipeline (1205)

============================== Vocab & Vectors ==============================
ℹ 14633 total word(s) in the data (2840 unique)
ℹ No word vectors present in the package

========================== Named Entity Recognition ==========================
ℹ 5 label(s)
0 missing value(s) (tokens with '-' label)
⚠ 115 entity span(s) with punctuation
⚠ Low number of examples for label 'EVENT' (11)
✔ Examples without occurrences available for all labels
✔ No entities consisting of or starting/ending with whitespace
Entity spans consisting of or starting/ending with punctuation can not be
trained w

### 7. 	🚀 🤖 Lancement de l'entraînement  

paramètre `-g 0` (si GPU)

In [ ]:
!python -m spacy train $CONFIG_BASE_FILLED -g -1 --output $OUTPUT_MODEL

ℹ Saving to output directory:
/drive/MyDrive/spaCy/output_models/v1_n4a/n4a_v1_lg_cnn_fr
ℹ Using CPU

=========================== Initializing pipeline ===========================
[2021-10-26 11:27:24,247] [INFO] Set up nlp object from config
[2021-10-26 11:27:24,259] [INFO] Pipeline: ['tok2vec', 'ner']
[2021-10-26 11:27:24,264] [INFO] Created vocabulary
[2021-10-26 11:27:24,265] [INFO] Finished initializing nlp object
[2021-10-26 11:27:26,067] [INFO] Initialized pipeline components: ['tok2vec', 'ner']
✔ Initialized pipeline

============================= Training pipeline =============================
ℹ Pipeline: ['tok2vec', 'ner']
ℹ Initial learn rate: 0.001
E    #       LOSS TOK2VEC  LOSS NER  ENTS_F  ENTS_P  ENTS_R  SCORE 
---  ------  ------------  --------  ------  ------  ------  ------
  0       0          0.00     51.68    0.00    0.00    0.00    0.00
  1     200        632.22   4175.26   58.65   65.84   52.88    0.59
  2     400        411.02   2049.09   67.83   71.39   64.60

### 8.📊 Évaluation du modèle 

In [ ]:
# a modifier selon où se trouve les données

model_eval="/drive/MyDrive/spaCy/output_models/v1_n4a/n4a_v1_lg_cnn_fr/model-best"
eval_file="/drive/MyDrive/spaCy/data/large/eval.spacy"
output_metrics="/drive/MyDrive/spaCy/output_models/v1_n4a/evaluations/metrics/n4a_v1_lg_cnn_fr" + ".json"
output_visualisations="/drive/MyDrive/spaCy/output_models/v1_n4a/evaluations/visualisations/"

In [ ]:
# If GPU : --gpu-id 0
!python -m spacy evaluate $model_eval $eval_file --output $output_metrics --gpu-id -1 --displacy-path $output_visualisations

ℹ Using CPU

================================== Results ==================================

TOK     -    
NER P   54.55
NER R   48.32
NER F   51.25
SPEED   19470


=============================== NER (per type) ===============================

                   P       R       F
ORGANISATION   30.00   23.08   26.09
PERSON         62.79   64.29   63.53
LOCATION       57.38   53.85   55.56
TITLE          66.67   26.67   38.10
EVENT           0.00    0.00    0.00

✔ Generated 25 parses as HTML
/drive/MyDrive/spaCy/output_models/v1_n4a/evaluations/visualisations
✔ Saved results to
/drive/MyDrive/spaCy/output_models/v1_n4a/evaluations/metrics/n4a_v1_lg_cnn_fr.json


### 9. 🧪 Tester le modèle NER "à la volée" / visualisation

In [ ]:
from spacy import displacy

# a modifier pour le texte d'évaluation
test_text = "/drive/MyDrive/spaCy/raw_texts/text_test_2.txt"

text = open(test_text, mode="r", encoding="utf-8").read()
sample = []
for line in text.splitlines():
   if line != "":
      sample.append(line)

nlp = spacy.load(model_eval)

doc = nlp(text)

opt_render = {
    "ents":["ORGANISATION", "LOCATION", "TITLE", "PERSON", "EVENT"],
    "colors":{
        "LOCATION":"#e74c3c",
        "ORGANISATION":"#9b59b6",
        "PERSON":"#45b39d",
        "TITLE":"#85c1e9",
        "EVENT":"#4d8fbb"
    }
}

displacy.render(doc, style="ent", jupyter=True, options=opt_render)